## Проект 5
Выбираем авто

## Цель проекта:
Создать модель, которая будет предсказывать стоимость автомобиля по его характеристикам.

## Алгоритм действий:
1. Собрать данные с помощью парсинга с сайта auto.ru  
    1.a. Собрать ссылки на объявления  
    1.b. На основе собранных ссылок собрать необходимые признаки, которые есть в тестовой выборке  
2. Обработать данные  
3. Провести анализ данных и определить, какие признаки использовать
4. Провести тесты различных моделей на приготовленной выборке
5. Выбрать лучшую модель и предсказать цены

## Импорт библиотек

In [2]:
# Загружаем библиотеки
import pandas as pd
import numpy as np
from pandas import Series

import pandas_profiling
from pandas_profiling import ProfileReport
import os
import requests  
from bs4 import BeautifulSoup
import time
import json
import re
from sklearn.preprocessing import LabelEncoder, OneHotEncoder, StandardScaler
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import KFold
from sklearn.base import clone
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import LabelEncoder
from sklearn.neighbors import KNeighborsRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.model_selection import RandomizedSearchCV
from sklearn.feature_selection import f_classif, mutual_info_classif
from catboost import CatBoostRegressor
from tqdm.notebook import tqdm
from sklearn.ensemble import StackingRegressor

from sklearn.feature_selection import f_classif, mutual_info_classif
from sklearn.preprocessing import LabelEncoder, OneHotEncoder, StandardScaler
# import xgboost as xgb

## Загрузка данных

In [4]:
# Загружаем тестовую выборку
test = pd.read_csv('test.csv')

## Предварительный анализ данных

### Описание признаков в тестовом датасете:
* bodyType - тип кузова
* brand - марка автомобиля
* car_url - сайт с объявлением
* color - цвет автомобиля
* complectation_dict - словарь с версией пакета комплектации автомобиля 
* description - дополнительное описание автомобиля / объявления
* engineDisplacement - объем двигателя
* enginePower - мощность двигателя
* equipment_dict - словарь с комплектацией автомобиля
* fuelType - тип топлива
* image - изображение
* mileage - пробег
* modelDate - год выпуска модели
* model_info - информация о модели в оригинале и по-русски
* model_name - название модели
* name - означение объема и типа двигателя, мощность в лошадиных силах
* numberOfDoors - кол-во дверей
* parsing_unixtime - дата парсинга данных
* priceCurrency - валюта
* productionDate - год производства
* sell_id - код (ID) продавца
* super_gen - словарь с технической характеристикой автомобиля
* vehicleConfiguration - кузов, количество дверей и объем двигателя транспортного средства
* vehicleTransmission - тип коробки передачи
* vendor - регион изготовителя: Европа или Япония
* Владельцы - кол-во владельцев
* Владение - срок владения
* ПТС - тип документа: оригинал или дупликат
* Привод - тип привода
* Руль - размещение руля
* Состояние - информация о том, требует ли ремонта автомобиль
* Таможня - информация о том, растаможено ли авто

In [5]:
profile = ProfileReport(test)
profile

Summarize dataset:   0%|          | 0/45 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

#### Комментарии по профайлингу
* В датасете присутствуют только 6 цифровых признаков. Сильно скореллированны между собой:  mileage, modelDate, productionDate. Между mileage и двумя остальными признаками присутствует отрицательная корреляция. Это логично, чем больше год производства или модели, тем меньше успел этот автомобиль проехать. Не смотря на сильную корреляцию пробега с позосталыми признаками, этот признак нужно оставить. Именно отличие от среднегодового пробега влияет на цену. Что касается даты выпуска модели и даты производства - возможно, на последующем этапе нужно будет оставить только один. Пока примем это во внимание.
* Есть необходимость на последующих этапах преобразовать категориальные признаки в числовые, бинарные и ординальные.
* Есть признаки, в которых присутствует только одно значение: валюта, состояние и таможня. Признак "валюта" не будем брать во внимание, остальные признаки - это, по всей видимости, фильтр пользовтеля. Необходимо учесть при приготовлении датасета
* Большое количество пропусков присутствует в completion_dict, equipment_dict, владение. На последующих этапах примем решение о преобразованиях этих признаков или исключении из анализа.

##  Парсинг Часть 1

Парсинг я разделил на 2 этапа:
1. Сбор ссылок на конкретные объявления
2. Парсинг необходимых признаков из перечня ссылок на объявления


Из предварительной обработки видно, что нет необходимости собирать информации о валюте, поскольку на сайте есть только одна валюта, а также ссылка на сайт объявления может иметь значение для пользователя, но в определении ключевый признаков нет смысла использовать, тем самым немного можно сократить ресурсы парсинга. Аналогично исключаем из анализа фотографии

In [17]:
# Создадим цикл для загрузки ссылок выбранной марки
url = 'https://auto.ru/moskva/cars/honda/used'
number_of_pages = 23

honda_links = []

for i in range(1, number_of_pages+1):
        print('Current Page:', i, 'Total Pages:', number_of_pages)
        url_page = url + '/?page=' + str(i)
        # print(url_page)
        res = requests.get(url_page)
        time.sleep(0.1)
        soup = BeautifulSoup(res.content.decode('utf-8'), 'html.parser')
        car_listing = soup.find_all('a', class_='Link ListingItemTitle__link')
        car_links = list(map(lambda x: x.get('href'), car_listing))
        for link in car_links:
            honda_links.append(link)
honda_links

Current Page: 1 Total Pages: 23
Current Page: 2 Total Pages: 23
Current Page: 3 Total Pages: 23
Current Page: 4 Total Pages: 23
Current Page: 5 Total Pages: 23
Current Page: 6 Total Pages: 23
Current Page: 7 Total Pages: 23
Current Page: 8 Total Pages: 23
Current Page: 9 Total Pages: 23
Current Page: 10 Total Pages: 23
Current Page: 11 Total Pages: 23
Current Page: 12 Total Pages: 23
Current Page: 13 Total Pages: 23
Current Page: 14 Total Pages: 23
Current Page: 15 Total Pages: 23
Current Page: 16 Total Pages: 23
Current Page: 17 Total Pages: 23
Current Page: 18 Total Pages: 23
Current Page: 19 Total Pages: 23
Current Page: 20 Total Pages: 23
Current Page: 21 Total Pages: 23
Current Page: 22 Total Pages: 23
Current Page: 23 Total Pages: 23


['https://auto.ru/cars/used/sale/honda/crosstour/1103946380-2f6fd560/',
 'https://auto.ru/cars/used/sale/honda/cr_v/1105251126-95d0b1bd/',
 'https://auto.ru/cars/used/sale/honda/pilot/1103731646-679cb26d/',
 'https://auto.ru/cars/used/sale/honda/cr_v/1105039682-d8878c18/',
 'https://auto.ru/cars/used/sale/honda/cr_v/1105274979-47523f56/',
 'https://auto.ru/cars/used/sale/honda/cr_v/1104922764-56e480c1/',
 'https://auto.ru/cars/used/sale/honda/civic/1105163834-6d2be73d/',
 'https://auto.ru/cars/used/sale/honda/cr_v/1104152441-f93c190b/',
 'https://auto.ru/cars/used/sale/honda/civic/1105280309-af489a01/',
 'https://auto.ru/cars/used/sale/honda/civic/1105277402-ad6c129a/',
 'https://auto.ru/cars/used/sale/honda/cr_v/1105325354-f8743462/',
 'https://auto.ru/cars/used/sale/honda/accord/1103904393-aebaaf4e/',
 'https://auto.ru/cars/used/sale/honda/cr_v/1105311443-bd81b2c1/',
 'https://auto.ru/cars/used/sale/honda/civic/1105214697-c26bb5f9/',
 'https://auto.ru/cars/used/sale/honda/fit/1104278

In [18]:
len(honda_links)

856

In [3]:
# Создаем функцию для определения количества страниц по каждой марке
def get_total_pages(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content.decode('utf-8'), 'html.parser')
    show_number = soup.find('span', class_ = 'ButtonWithLoader__content').text
    number_total = show_number.replace(u'\xa0', u' ').split()[1:3]
    number_total = int(''.join(number_total))
    pages_total = int(number_total/38)
    
    return pages_total

In [4]:
# Проверяем на BMW
get_total_pages('https://auto.ru/moskva/cars/bmw/used')

122

In [5]:
# Проверяем на Skoda
get_total_pages('https://auto.ru/moskva/cars/skoda/used')

60

In [8]:
# Создаем цикл сбора ссылок по выбранной марке
url = 'https://auto.ru/moskva/cars/bmw/used'
number_of_pages = get_total_pages(url)

bmw_links = []

for i in range(1, number_of_pages+1):
        print('Current Page:', i, 'Total Pages:', number_of_pages)
        url_page = url + '/?page=' + str(i)
        # print(url_page)
        res = requests.get(url_page)
        time.sleep(0.2)
        soup = BeautifulSoup(res.content.decode('utf-8'), 'html.parser')
        car_listing = soup.find_all('a', class_='Link ListingItemTitle__link')
        car_links = list(map(lambda x: x.get('href'), car_listing))
        for link in car_links:
            bmw_links.append(link)
bmw_links

Current Page: 1 Total Pages: 121
Current Page: 2 Total Pages: 121
Current Page: 3 Total Pages: 121
Current Page: 4 Total Pages: 121
Current Page: 5 Total Pages: 121
Current Page: 6 Total Pages: 121
Current Page: 7 Total Pages: 121
Current Page: 8 Total Pages: 121
Current Page: 9 Total Pages: 121
Current Page: 10 Total Pages: 121
Current Page: 11 Total Pages: 121
Current Page: 12 Total Pages: 121
Current Page: 13 Total Pages: 121
Current Page: 14 Total Pages: 121
Current Page: 15 Total Pages: 121
Current Page: 16 Total Pages: 121
Current Page: 17 Total Pages: 121
Current Page: 18 Total Pages: 121
Current Page: 19 Total Pages: 121
Current Page: 20 Total Pages: 121
Current Page: 21 Total Pages: 121
Current Page: 22 Total Pages: 121
Current Page: 23 Total Pages: 121
Current Page: 24 Total Pages: 121
Current Page: 25 Total Pages: 121
Current Page: 26 Total Pages: 121
Current Page: 27 Total Pages: 121
Current Page: 28 Total Pages: 121
Current Page: 29 Total Pages: 121
Current Page: 30 Total 

['https://auto.ru/cars/used/sale/bmw/5er/1104750723-ce3c5ad8/',
 'https://auto.ru/cars/used/sale/bmw/5er/1105005872-6e38bded/',
 'https://auto.ru/cars/used/sale/bmw/m3/1104915593-3f08f223/',
 'https://auto.ru/cars/used/sale/bmw/x5/1105209181-8d455f5d/',
 'https://auto.ru/cars/used/sale/bmw/5er/1104924661-296aae04/',
 'https://auto.ru/cars/used/sale/bmw/x6_m/1105314239-1df0c417/',
 'https://auto.ru/cars/used/sale/bmw/x2/1104098388-0d6366dd/',
 'https://auto.ru/cars/used/sale/bmw/x3/1104239387-03022c6a/',
 'https://auto.ru/cars/used/sale/bmw/1er/1105173469-8906d80d/',
 'https://auto.ru/cars/used/sale/bmw/x1/1104041254-e2f7ddbd/',
 'https://auto.ru/cars/used/sale/bmw/x6_m/1104660218-f138a6aa/',
 'https://auto.ru/cars/used/sale/bmw/7er/1105265499-1b5d2aa9/',
 'https://auto.ru/cars/used/sale/bmw/5er/1105324917-1756e77c/',
 'https://auto.ru/cars/used/sale/bmw/3er/1103663300-ab22f804/',
 'https://auto.ru/cars/used/sale/bmw/3er/1105312487-f7202707/',
 'https://auto.ru/cars/used/sale/bmw/5er/11

In [13]:
len(bmw_links)

4515

In [11]:
url = 'https://auto.ru/moskva/cars/volkswagen/used'
number_of_pages = get_total_pages(url)

vw_links = []

for i in range(1, number_of_pages+1):
        print('Current Page:', i, 'Total Pages:', number_of_pages)
        url_page = url + '/?page=' + str(i)
        # print(url_page)
        res = requests.get(url_page)
        time.sleep(0.2)
        soup = BeautifulSoup(res.content.decode('utf-8'), 'html.parser')
        car_listing = soup.find_all('a', class_='Link ListingItemTitle__link')
        car_links = list(map(lambda x: x.get('href'), car_listing))
        for link in car_links:
            vw_links.append(link)
vw_links

Current Page: 1 Total Pages: 114
Current Page: 2 Total Pages: 114
Current Page: 3 Total Pages: 114
Current Page: 4 Total Pages: 114
Current Page: 5 Total Pages: 114
Current Page: 6 Total Pages: 114
Current Page: 7 Total Pages: 114
Current Page: 8 Total Pages: 114
Current Page: 9 Total Pages: 114
Current Page: 10 Total Pages: 114
Current Page: 11 Total Pages: 114
Current Page: 12 Total Pages: 114
Current Page: 13 Total Pages: 114
Current Page: 14 Total Pages: 114
Current Page: 15 Total Pages: 114
Current Page: 16 Total Pages: 114
Current Page: 17 Total Pages: 114
Current Page: 18 Total Pages: 114
Current Page: 19 Total Pages: 114
Current Page: 20 Total Pages: 114
Current Page: 21 Total Pages: 114
Current Page: 22 Total Pages: 114
Current Page: 23 Total Pages: 114
Current Page: 24 Total Pages: 114
Current Page: 25 Total Pages: 114
Current Page: 26 Total Pages: 114
Current Page: 27 Total Pages: 114
Current Page: 28 Total Pages: 114
Current Page: 29 Total Pages: 114
Current Page: 30 Total 

['https://auto.ru/cars/used/sale/volkswagen/golf/1105112533-90a034f9/',
 'https://auto.ru/cars/used/sale/volkswagen/passat/1105223868-686b4f51/',
 'https://auto.ru/cars/used/sale/volkswagen/tiguan/1105146351-f84aaf02/',
 'https://auto.ru/cars/used/sale/volkswagen/passat/1105161061-eac37ee0/',
 'https://auto.ru/cars/used/sale/volkswagen/passat/1104763761-2de60c1a/',
 'https://auto.ru/cars/used/sale/volkswagen/tiguan/1105185389-9e4a4861/',
 'https://auto.ru/cars/used/sale/volkswagen/golf/1104870548-08586fe2/',
 'https://auto.ru/cars/used/sale/volkswagen/jetta/1105087744-b91dbd12/',
 'https://auto.ru/cars/used/sale/volkswagen/passat/1104911094-cdb1ae4e/',
 'https://auto.ru/cars/used/sale/volkswagen/polo/1103098004-595d64bd/',
 'https://auto.ru/cars/used/sale/volkswagen/caddy/1105314728-6d2fa918/',
 'https://auto.ru/cars/used/sale/volkswagen/touareg/1105314291-8535f144/',
 'https://auto.ru/cars/used/sale/volkswagen/jetta/1105177059-a98a2ea2/',
 'https://auto.ru/cars/used/sale/volkswagen/pa

In [12]:
len(vw_links)

4249

In [14]:
url = 'https://auto.ru/moskva/cars/MITSUBISHI/used'
number_of_pages = get_total_pages(url)

mitsu_links = []

for i in range(1, number_of_pages+1):
        print('Current Page:', i, 'Total Pages:', number_of_pages)
        url_page = url + '/?page=' + str(i)
        # print(url_page)
        res = requests.get(url_page)
        time.sleep(0.2)
        soup = BeautifulSoup(res.content.decode('utf-8'), 'html.parser')
        car_listing = soup.find_all('a', class_='Link ListingItemTitle__link')
        car_links = list(map(lambda x: x.get('href'), car_listing))
        for link in car_links:
            mitsu_links.append(link)
mitsu_links

Current Page: 1 Total Pages: 61
Current Page: 2 Total Pages: 61
Current Page: 3 Total Pages: 61
Current Page: 4 Total Pages: 61
Current Page: 5 Total Pages: 61
Current Page: 6 Total Pages: 61
Current Page: 7 Total Pages: 61
Current Page: 8 Total Pages: 61
Current Page: 9 Total Pages: 61
Current Page: 10 Total Pages: 61
Current Page: 11 Total Pages: 61
Current Page: 12 Total Pages: 61
Current Page: 13 Total Pages: 61
Current Page: 14 Total Pages: 61
Current Page: 15 Total Pages: 61
Current Page: 16 Total Pages: 61
Current Page: 17 Total Pages: 61
Current Page: 18 Total Pages: 61
Current Page: 19 Total Pages: 61
Current Page: 20 Total Pages: 61
Current Page: 21 Total Pages: 61
Current Page: 22 Total Pages: 61
Current Page: 23 Total Pages: 61
Current Page: 24 Total Pages: 61
Current Page: 25 Total Pages: 61
Current Page: 26 Total Pages: 61
Current Page: 27 Total Pages: 61
Current Page: 28 Total Pages: 61
Current Page: 29 Total Pages: 61
Current Page: 30 Total Pages: 61
Current Page: 31 To

['https://auto.ru/cars/used/sale/mitsubishi/asx/1104842727-248e95a1/',
 'https://auto.ru/cars/used/sale/mitsubishi/outlander/1105267814-421c6c48/',
 'https://auto.ru/cars/used/sale/mitsubishi/pajero_sport/1105314274-2802cf08/',
 'https://auto.ru/cars/used/sale/mitsubishi/outlander/1104990172-86fbe6a9/',
 'https://auto.ru/cars/used/sale/mitsubishi/outlander/1104802966-b9072b48/',
 'https://auto.ru/cars/used/sale/mitsubishi/pajero_sport/1105192550-4c180b67/',
 'https://auto.ru/cars/used/sale/mitsubishi/lancer/1105261134-bd3cabd0/',
 'https://auto.ru/cars/used/sale/mitsubishi/pajero_sport/1105291618-4421891f/',
 'https://auto.ru/cars/used/sale/mitsubishi/outlander/1105156068-e34d2abc/',
 'https://auto.ru/cars/used/sale/mitsubishi/outlander/1105275688-9b0a3907/',
 'https://auto.ru/cars/used/sale/mitsubishi/lancer/1105230926-fdec25e9/',
 'https://auto.ru/cars/used/sale/mitsubishi/outlander/1105039685-4228e746/',
 'https://auto.ru/cars/used/sale/mitsubishi/lancer/1105089929-72e389be/',
 'htt

In [15]:
len(mitsu_links)

2268

In [21]:

skoda_links

Current Page: 1 Total Pages: 60
Current Page: 2 Total Pages: 60
Current Page: 3 Total Pages: 60
Current Page: 4 Total Pages: 60
Current Page: 5 Total Pages: 60
Current Page: 6 Total Pages: 60
Current Page: 7 Total Pages: 60
Current Page: 8 Total Pages: 60
Current Page: 9 Total Pages: 60
Current Page: 10 Total Pages: 60
Current Page: 11 Total Pages: 60
Current Page: 12 Total Pages: 60
Current Page: 13 Total Pages: 60
Current Page: 14 Total Pages: 60
Current Page: 15 Total Pages: 60
Current Page: 16 Total Pages: 60
Current Page: 17 Total Pages: 60
Current Page: 18 Total Pages: 60
Current Page: 19 Total Pages: 60
Current Page: 20 Total Pages: 60
Current Page: 21 Total Pages: 60
Current Page: 22 Total Pages: 60
Current Page: 23 Total Pages: 60
Current Page: 24 Total Pages: 60
Current Page: 25 Total Pages: 60
Current Page: 26 Total Pages: 60
Current Page: 27 Total Pages: 60
Current Page: 28 Total Pages: 60
Current Page: 29 Total Pages: 60
Current Page: 30 Total Pages: 60
Current Page: 31 To

['https://auto.ru/cars/used/sale/skoda/octavia/1105314148-346b0ae3/',
 'https://auto.ru/cars/used/sale/skoda/roomster/1105209881-dceab6cb/',
 'https://auto.ru/cars/used/sale/skoda/octavia/1105272994-6f212ec3/',
 'https://auto.ru/cars/used/sale/skoda/rapid/1105152040-861334fc/',
 'https://auto.ru/cars/used/sale/skoda/yeti/1105231228-6bd4d7a2/',
 'https://auto.ru/cars/used/sale/skoda/rapid/1104711166-ba421fad/',
 'https://auto.ru/cars/used/sale/skoda/octavia/1104066995-85fe8abb/',
 'https://auto.ru/cars/used/sale/skoda/octavia/1105046410-4c877bf7/',
 'https://auto.ru/cars/used/sale/skoda/octavia/1105007376-7f777d32/',
 'https://auto.ru/cars/used/sale/skoda/octavia/1105046389-a6aec56d/',
 'https://auto.ru/cars/used/sale/skoda/fabia/1104182921-dd239029/',
 'https://auto.ru/cars/used/sale/skoda/rapid/1105221917-1f88586f/',
 'https://auto.ru/cars/used/sale/skoda/octavia/1105222045-601d92a5/',
 'https://auto.ru/cars/used/sale/skoda/octavia/1105222014-21b5c714/',
 'https://auto.ru/cars/used/sa

In [22]:
len(skoda_links)

2228

In [26]:
url = 'https://auto.ru/moskva/cars/infiniti/used'
number_of_pages = 16

infi_links = []

for i in range(1, number_of_pages+1):
        print('Current Page:', i, 'Total Pages:', number_of_pages)
        url_page = url + '/?page=' + str(i)
        # print(url_page)
        res = requests.get(url_page)
        time.sleep(0.1)
        soup = BeautifulSoup(res.content.decode('utf-8'), 'html.parser')
        car_listing = soup.find_all('a', class_='Link ListingItemTitle__link')
        car_links = list(map(lambda x: x.get('href'), car_listing))
        for link in car_links:
            infi_links.append(link)
infi_links

Current Page: 1 Total Pages: 16
Current Page: 2 Total Pages: 16
Current Page: 3 Total Pages: 16
Current Page: 4 Total Pages: 16
Current Page: 5 Total Pages: 16
Current Page: 6 Total Pages: 16
Current Page: 7 Total Pages: 16
Current Page: 8 Total Pages: 16
Current Page: 9 Total Pages: 16
Current Page: 10 Total Pages: 16
Current Page: 11 Total Pages: 16
Current Page: 12 Total Pages: 16
Current Page: 13 Total Pages: 16
Current Page: 14 Total Pages: 16
Current Page: 15 Total Pages: 16
Current Page: 16 Total Pages: 16


['https://auto.ru/cars/used/sale/infiniti/qx50/1105264974-e4422bd9/',
 'https://auto.ru/cars/used/sale/infiniti/g35/1104811194-97f5dd11/',
 'https://auto.ru/cars/used/sale/infiniti/qx60/1103356157-4874d2da/',
 'https://auto.ru/cars/used/sale/infiniti/m/1105275119-a36ff5f3/',
 'https://auto.ru/cars/used/sale/infiniti/fx/1105326710-ea2dfff6/',
 'https://auto.ru/cars/used/sale/infiniti/fx/1105269608-6eec1dc4/',
 'https://auto.ru/cars/used/sale/infiniti/fx/1104651945-cb4558b3/',
 'https://auto.ru/cars/used/sale/infiniti/fx/1104984663-a06b9bff/',
 'https://auto.ru/cars/used/sale/infiniti/jx/1105323612-cbf32937/',
 'https://auto.ru/cars/used/sale/infiniti/ex/1105214618-b2bccc2e/',
 'https://auto.ru/cars/used/sale/infiniti/g35/1105099379-a815cc99/',
 'https://auto.ru/cars/used/sale/infiniti/qx50/1105323082-52df4e39/',
 'https://auto.ru/cars/used/sale/infiniti/qx70/1105323453-dc20de49/',
 'https://auto.ru/cars/used/sale/infiniti/g35/1104902640-1e7dd64d/',
 'https://auto.ru/cars/used/sale/infin

In [27]:
len(infi_links)

593

In [28]:
# Создаем цикл по сбору ссылок интереcующих нас марок

# Выбираем оставшиеся марки, которые присутствуют в тестовой выборке
brands = ['AUDI','VOLVO', 'NISSAN',
       'MERCEDES', 'TOYOTA', 'LEXUS',]

url_list = ['https://auto.ru/moskva/cars/'+brand+'/used' for brand in brands]

rest_moscow_links = []

for url in url_list:
    number_of_pages = get_total_pages(url)
    for i in range(1, number_of_pages+1):
        print('Current Page:', i, 'Brand:', url)
        url_page = url + '/?page=' + str(i)
        # print(url_page)
        res = requests.get(url_page)
        time.sleep(0.1)
        soup = BeautifulSoup(res.content.decode('utf-8'), 'html.parser')
        car_listing = soup.find_all('a', class_='Link ListingItemTitle__link')
        car_links = list(map(lambda x: x.get('href'), car_listing))
        # print(car_link)
        for link in car_links:
            rest_moscow_links.append(link)
    
rest_moscow_links

Current Page: 1 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 2 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 3 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 4 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 5 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 6 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 7 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 8 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 9 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 10 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 11 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 12 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 13 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 14 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 15 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 16 Brand: https://auto.ru/moskva/cars/AUDI/used
Current Page: 17 

Current Page: 33 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 34 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 35 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 36 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 37 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 38 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 39 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 40 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 41 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 42 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 43 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 44 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 45 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 46 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 47 Brand: https://auto.ru/moskva/cars/NISSAN/used
Current Page: 48 Brand: https://auto.ru/

Current Page: 76 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 77 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 78 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 79 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 80 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 81 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 82 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 83 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 84 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 85 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 86 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 87 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 88 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 89 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Page: 90 Brand: https://auto.ru/moskva/cars/MERCEDES/used
Current Pa

Current Page: 60 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 61 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 62 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 63 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 64 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 65 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 66 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 67 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 68 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 69 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 70 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 71 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 72 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 73 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 74 Brand: https://auto.ru/moskva/cars/TOYOTA/used
Current Page: 75 Brand: https://auto.ru/

['https://auto.ru/cars/used/sale/audi/rs5/1105298981-af473200/',
 'https://auto.ru/cars/used/sale/audi/tt_rs/1104881987-0020cda1/',
 'https://auto.ru/cars/used/sale/audi/a4/1104014027-5e64383d/',
 'https://auto.ru/cars/used/sale/audi/q5/1102408053-1ff62832/',
 'https://auto.ru/cars/used/sale/audi/a8/1104648548-28f2c0df/',
 'https://auto.ru/cars/used/sale/audi/a4/1105213919-2482d9f6/',
 'https://auto.ru/cars/used/sale/audi/a6/1104911672-d7462864/',
 'https://auto.ru/cars/used/sale/audi/q7/1105275622-69cd3dc3/',
 'https://auto.ru/cars/used/sale/audi/q7/1105249299-29138f4b/',
 'https://auto.ru/cars/used/sale/audi/q5/1104660642-81f7a495/',
 'https://auto.ru/cars/used/sale/audi/a5/1104763309-517949a4/',
 'https://auto.ru/cars/used/sale/audi/a5/1105173496-77a75fc5/',
 'https://auto.ru/cars/used/sale/audi/a3/1104884267-d102809e/',
 'https://auto.ru/cars/used/sale/audi/q3/1104825421-db2b7bcc/',
 'https://auto.ru/cars/used/sale/audi/q5/1105046388-2bbed7e2/',
 'https://auto.ru/cars/used/sale/aud

In [29]:
len(rest_moscow_links)

16598

In [30]:
moscow_links = bmw_links + vw_links + mitsu_links + skoda_links + infi_links + rest_moscow_links

In [31]:
len(moscow_links)

30451

In [32]:
with open('moscow_links.csv', 'a') as myfile:
        writer = csv.writer(myfile)
        for row in moscow_links:
            writer.writerow([row])

In [33]:
# Проверяем, правильно ли сохранились данные
test_links = pd.read_csv('moscow_links.csv',header=None)

In [34]:
test_links

0
0      https://auto.ru/cars/used/sale/bmw/5er/1104750...
1      https://auto.ru/cars/used/sale/bmw/5er/1105005...
2      https://auto.ru/cars/used/sale/bmw/m3/11049155...
3      https://auto.ru/cars/used/sale/bmw/x5/11052091...
4      https://auto.ru/cars/used/sale/bmw/5er/1104924...
...                                                  ...
30446  https://auto.ru/cars/used/sale/lexus/is/110410...
30447  https://auto.ru/cars/used/sale/lexus/ls/110358...
30448  https://auto.ru/cars/used/sale/lexus/gs/110495...
30449  https://auto.ru/cars/used/sale/lexus/ls/110507...
30450  https://auto.ru/cars/used/sale/lexus/lx/110421...

[30451 rows x 1 columns]

In [35]:
# Проверяем, правильно ли сохранились данные
test_links = pd.read_csv('links.csv',header=None)

In [36]:
test_links

0
0      https://auto.ru/cars/used/sale/bmw/5er/1104750...
1      https://auto.ru/cars/used/sale/bmw/5er/1105005...
2      https://auto.ru/cars/used/sale/bmw/m3/11049155...
3      https://auto.ru/cars/used/sale/bmw/x5/11052091...
4      https://auto.ru/cars/used/sale/bmw/5er/1104924...
...                                                  ...
30446  https://auto.ru/cars/used/sale/lexus/is/110410...
30447  https://auto.ru/cars/used/sale/lexus/ls/110358...
30448  https://auto.ru/cars/used/sale/lexus/gs/110495...
30449  https://auto.ru/cars/used/sale/lexus/ls/110507...
30450  https://auto.ru/cars/used/sale/lexus/lx/110421...

[30451 rows x 1 columns]